In [4]:
import sys
sys.path.append('..')
sys.path.append('../..')

import numpy as np
from datetime import datetime
import matplotlib.pyplot as plt
import pandas as pd, numpy as np, gc
from tqdm import tqdm
import joblib

from core import config as conf
from utils.dataiter import Dataiter


from collections import defaultdict
from sklearn import preprocessing
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras import optimizers
from sklearn.preprocessing import LabelEncoder, MinMaxScaler
from tensorflow.keras.models import save_model,load_model
import tensorflow as tf
import os

import numpy as np
from utils.preprocessing import *

In [ ]:
df = df[:10]

In [ ]:
df.to_csv('/dataset/final_data/small_dataset/part-valid_10', index=False, header=None)

In [ ]:
path = '/dataset/final_data/small_dataset/part-valid_10'
df = read_data(path)

In [ ]:
df

In [5]:
import os

from utils.dataiter import Dataset
from utils.preprocessing import *
from models.baseline.random_model import random_prediction_model
from models.model.Ensemble_FFNN_ALL import Ensemble_FFNN_ALL
# from models.model.XGBoost import XGBoost
from core.config import raw_features
import core.config as conf
from tqdm import tqdm

all_features_to_idx = dict(zip(raw_features, range(len(raw_features))))
float_formatter = "{:.15f}".format

def parse_input_line(line):
    features = line.split("\x01")
    tweet_id = features[all_features_to_idx['tweet_id']]
    user_id = features[all_features_to_idx['engager_id']]
    input_feats = features[all_features_to_idx['text_tokens']]
    return tweet_id, user_id, input_feats

In [6]:


path = '/dataset/final_data/small_dataset/'
model_path = conf.model_path


part_files = sorted([os.path.join(path, f) for f in os.listdir(path) if 'part' in f])
ds = Dataset()
file = path
with open('results.csv', 'w') as output:
    for file in tqdm(part_files):
        print(file)
        df = read_data(file)
        print(df.columns)
        df = ds.preprocess(df, TARGET_id=conf.REPLY)

        df = ds.tweet_engagements(df) # tweet engagement
        print('1')
        df = ds.user_engagements(df) # user engagement
        print('2')
        df = ds.tweet_features(df) # tweet features
        print('3')
        df = ds.set_engager_follows_creator(df) 
        print('4')

        pred_reply = Ensemble_FFNN_ALL(df, conf.REPLY).predict(model_path, model_num=0) 
        pred_retweet = Ensemble_FFNN_ALL(df, conf.RETWEET).predict(model_path, model_num=0) 
        pred_comment = Ensemble_FFNN_ALL(df, conf.COMMNET).predict(model_path, model_num=0) 
        pred_like = Ensemble_FFNN_ALL(df, conf.LIKE).predict(model_path, model_num=0) 

        with open(file, 'r') as f:
            for i, line in enumerate(f.readlines()):
                tweet_id, user_id, features = parse_input_line(line)
                '''
                ## XGBoost
                reply_pred = pred_reply[i]
                retweet_pred = pred_retweet[i]
                quote_pred = pred_comment[i]
                fav_pred = pred_like[i]
                '''
                print(pred_reply)
                reply_pred = pred_reply[i][0]
                retweet_pred = pred_retweet[i][0]
                quote_pred = pred_comment[i][0]
                fav_pred = pred_like[i][0]

                output.write(f'{tweet_id},{user_id},{reply_pred},{retweet_pred},{quote_pred},{fav_pred}\n')




  0%|          | 0/1 [00:00<?, ?it/s]

/dataset/final_data/small_dataset/part-valid_1000
Index(['text_tokens', 'hashtags', 'tweet_id', 'media', 'links', 'domains',
       'tweet_type', 'language', 'tweet_timestamp', 'creator_id',
       'creator_follower_count', 'creator_following_count',
       'creator_is_verified', 'creator_account_creation', 'engager_id',
       'engager_follower_count', 'engager_following_count',
       'engager_is_verified', 'engager_account_creation',
       'creator_follows_engager', 'reply_timestamp', 'retweet_timestamp',
       'comment_timestamp', 'like_timestamp'],
      dtype='object')
1
2
3


../../utils/dataset.py:476: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['engager_follows_creator'] = df.apply(lambda x : 1 if len(engager_follows_creator[x['engager_id']]) > 0 and x['creator_id'] in engager_follows_creator[x['engager_id']]  else 0.5, axis = 1)


4
------ predict ensemble model 0 ------
------ predict ensemble model 1 ------
------ predict ensemble model 2 ------
------ predict ensemble model 3 ------
------ predict ensemble model 4 ------
------ predict ensemble model 0 ------
------ predict ensemble model 1 ------
------ predict ensemble model 2 ------
------ predict ensemble model 3 ------
------ predict ensemble model 4 ------
------ predict ensemble model 0 ------
------ predict ensemble model 1 ------
------ predict ensemble model 2 ------
------ predict ensemble model 3 ------
------ predict ensemble model 4 ------
------ predict ensemble model 0 ------
------ predict ensemble model 1 ------
------ predict ensemble model 2 ------
------ predict ensemble model 3 ------
------ predict ensemble model 4 ------
[[7.69061074e-02]
 [2.78240032e-02]
 [8.15348849e-02]
 [4.23798570e-03]
 [6.32273480e-02]
 [2.77538188e-02]
 [3.19729932e-02]
 [2.88075693e-02]
 [3.40305679e-02]
 [3.28193195e-02]
 [5.94242197e-03]
 [1.55354682e-02]
 [

 [9.97158000e-04]]
[[7.69061074e-02]
 [2.78240032e-02]
 [8.15348849e-02]
 [4.23798570e-03]
 [6.32273480e-02]
 [2.77538188e-02]
 [3.19729932e-02]
 [2.88075693e-02]
 [3.40305679e-02]
 [3.28193195e-02]
 [5.94242197e-03]
 [1.55354682e-02]
 [4.20560222e-03]
 [1.32539691e-02]
 [3.49607989e-02]
 [3.14167747e-03]
 [2.07853923e-03]
 [1.45673081e-01]
 [4.15911060e-03]
 [1.82729959e-03]
 [3.58980289e-03]
 [1.52375521e-02]
 [3.95928398e-02]
 [2.58703046e-02]
 [1.48424329e-02]
 [4.63386765e-03]
 [4.56804410e-02]
 [5.11535779e-02]
 [9.46626514e-02]
 [1.52462721e-03]
 [7.26705492e-02]
 [5.44235185e-02]
 [7.90604651e-02]
 [5.04608173e-03]
 [8.66717100e-03]
 [4.33241129e-02]
 [1.24368665e-03]
 [3.07613127e-02]
 [1.12386741e-01]
 [5.68885580e-02]
 [1.65096968e-01]
 [2.15473166e-03]
 [5.01381457e-02]
 [3.54988277e-02]
 [7.67059904e-03]
 [2.90415473e-02]
 [4.52706330e-02]
 [1.25803515e-01]
 [2.98616178e-02]
 [2.01240182e-03]
 [4.02977988e-02]
 [1.11509142e-02]
 [1.54514655e-01]
 [1.41599181e-03]
 [1.05339

...

[[7.69061074e-02]
 [2.78240032e-02]
 [8.15348849e-02]
 [4.23798570e-03]
 [6.32273480e-02]
 [2.77538188e-02]
 [3.19729932e-02]
 [2.88075693e-02]
 [3.40305679e-02]
 [3.28193195e-02]
 [5.94242197e-03]
 [1.55354682e-02]
 [4.20560222e-03]
 [1.32539691e-02]
 [3.49607989e-02]
 [3.14167747e-03]
 [2.07853923e-03]
 [1.45673081e-01]
 [4.15911060e-03]
 [1.82729959e-03]
 [3.58980289e-03]
 [1.52375521e-02]
 [3.95928398e-02]
 [2.58703046e-02]
 [1.48424329e-02]
 [4.63386765e-03]
 [4.56804410e-02]
 [5.11535779e-02]
 [9.46626514e-02]
 [1.52462721e-03]
 [7.26705492e-02]
 [5.44235185e-02]
 [7.90604651e-02]
 [5.04608173e-03]
 [8.66717100e-03]
 [4.33241129e-02]
 [1.24368665e-03]
 [3.07613127e-02]
 [1.12386741e-01]
 [5.68885580e-02]
 [1.65096968e-01]
 [2.15473166e-03]
 [5.01381457e-02]
 [3.54988277e-02]
 [7.67059904e-03]
 [2.90415473e-02]
 [4.52706330e-02]
 [1.25803515e-01]
 [2.98616178e-02]
 [2.01240182e-03]
 [4.02977988e-02]
 [1.11509142e-02]
 [1.54514655e-01]
 [1.41599181e-03]
 [1.05339810e-01]
 [5.227281

[[7.69061074e-02]
 [2.78240032e-02]
 [8.15348849e-02]
 [4.23798570e-03]
 [6.32273480e-02]
 [2.77538188e-02]
 [3.19729932e-02]
 [2.88075693e-02]
 [3.40305679e-02]
 [3.28193195e-02]
 [5.94242197e-03]
 [1.55354682e-02]
 [4.20560222e-03]
 [1.32539691e-02]
 [3.49607989e-02]
 [3.14167747e-03]
 [2.07853923e-03]
 [1.45673081e-01]
 [4.15911060e-03]
 [1.82729959e-03]
 [3.58980289e-03]
 [1.52375521e-02]
 [3.95928398e-02]
 [2.58703046e-02]
 [1.48424329e-02]
 [4.63386765e-03]
 [4.56804410e-02]
 [5.11535779e-02]
 [9.46626514e-02]
 [1.52462721e-03]
 [7.26705492e-02]
 [5.44235185e-02]
 [7.90604651e-02]
 [5.04608173e-03]
 [8.66717100e-03]
 [4.33241129e-02]
 [1.24368665e-03]
 [3.07613127e-02]
 [1.12386741e-01]
 [5.68885580e-02]
 [1.65096968e-01]
 [2.15473166e-03]
 [5.01381457e-02]
 [3.54988277e-02]
 [7.67059904e-03]
 [2.90415473e-02]
 [4.52706330e-02]
 [1.25803515e-01]
 [2.98616178e-02]
 [2.01240182e-03]
 [4.02977988e-02]
 [1.11509142e-02]
 [1.54514655e-01]
 [1.41599181e-03]
 [1.05339810e-01]
 [5.227281

[[7.69061074e-02]
 [2.78240032e-02]
 [8.15348849e-02]
 [4.23798570e-03]
 [6.32273480e-02]
 [2.77538188e-02]
 [3.19729932e-02]
 [2.88075693e-02]
 [3.40305679e-02]
 [3.28193195e-02]
 [5.94242197e-03]
 [1.55354682e-02]
 [4.20560222e-03]
 [1.32539691e-02]
 [3.49607989e-02]
 [3.14167747e-03]
 [2.07853923e-03]
 [1.45673081e-01]
 [4.15911060e-03]
 [1.82729959e-03]
 [3.58980289e-03]
 [1.52375521e-02]
 [3.95928398e-02]
 [2.58703046e-02]
 [1.48424329e-02]
 [4.63386765e-03]
 [4.56804410e-02]
 [5.11535779e-02]
 [9.46626514e-02]
 [1.52462721e-03]
 [7.26705492e-02]
 [5.44235185e-02]
 [7.90604651e-02]
 [5.04608173e-03]
 [8.66717100e-03]
 [4.33241129e-02]
 [1.24368665e-03]
 [3.07613127e-02]
 [1.12386741e-01]
 [5.68885580e-02]
 [1.65096968e-01]
 [2.15473166e-03]
 [5.01381457e-02]
 [3.54988277e-02]
 [7.67059904e-03]
 [2.90415473e-02]
 [4.52706330e-02]
 [1.25803515e-01]
 [2.98616178e-02]
 [2.01240182e-03]
 [4.02977988e-02]
 [1.11509142e-02]
 [1.54514655e-01]
 [1.41599181e-03]
 [1.05339810e-01]
 [5.227281

[[7.69061074e-02]
 [2.78240032e-02]
 [8.15348849e-02]
 [4.23798570e-03]
 [6.32273480e-02]
 [2.77538188e-02]
 [3.19729932e-02]
 [2.88075693e-02]
 [3.40305679e-02]
 [3.28193195e-02]
 [5.94242197e-03]
 [1.55354682e-02]
 [4.20560222e-03]
 [1.32539691e-02]
 [3.49607989e-02]
 [3.14167747e-03]
 [2.07853923e-03]
 [1.45673081e-01]
 [4.15911060e-03]
 [1.82729959e-03]
 [3.58980289e-03]
 [1.52375521e-02]
 [3.95928398e-02]
 [2.58703046e-02]
 [1.48424329e-02]
 [4.63386765e-03]
 [4.56804410e-02]
 [5.11535779e-02]
 [9.46626514e-02]
 [1.52462721e-03]
 [7.26705492e-02]
 [5.44235185e-02]
 [7.90604651e-02]
 [5.04608173e-03]
 [8.66717100e-03]
 [4.33241129e-02]
 [1.24368665e-03]
 [3.07613127e-02]
 [1.12386741e-01]
 [5.68885580e-02]
 [1.65096968e-01]
 [2.15473166e-03]
 [5.01381457e-02]
 [3.54988277e-02]
 [7.67059904e-03]
 [2.90415473e-02]
 [4.52706330e-02]
 [1.25803515e-01]
 [2.98616178e-02]
 [2.01240182e-03]
 [4.02977988e-02]
 [1.11509142e-02]
 [1.54514655e-01]
 [1.41599181e-03]
 [1.05339810e-01]
 [5.227281

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [44]:
engager_follows_creator_path = conf.pickle_data + "engager_follows_creator_2.pkl"

if os.path.exists(engager_follows_creator_path ) :
    with open(engager_follows_creator_path, 'rb') as f :
        engager_follows_creator = pickle.load(f)
        engager_follows_creator = defaultdict(lambda : {}, engager_follows_creator)
df['engager_follows_creator'] = df.apply(lambda x : 1 if len(engager_follows_creator[x['engager_id']]) > 0 and x['creator_id'] in engager_follows_creator[x['engager_id']]  else 0.5, axis = 1)



In [43]:
engager_follows_creator['7D3C3D00D14613287ABC9C140FE26A54']

set

In [45]:
df['engager_follows_creator'] = df.apply(lambda x : 1 if len(engager_follows_creator[x['engager_id']]) > 0 and x['creator_id'] in engager_follows_creator[x['engager_id']]  else 0.5, axis = 1)




In [48]:
a = df[df['engager_follows_creator'] != 0.5]
b = df[df['engager_follows_creator'] == 0.5]

In [52]:
engager_follows_creator_path = conf.pickle_data + "not_engager_follows_creator_2.pkl"

if os.path.exists(engager_follows_creator_path ) :
    with open(engager_follows_creator_path, 'rb') as f :
        engager_follows_creator = pickle.load(f)
        engager_follows_creator = defaultdict(lambda : {}, engager_follows_creator)




In [61]:
engager_follows_creator['F16C923EEEF0C56FA8E03C9947A70CAB']

{}

In [55]:
b['engager_follows_creator'] = df.apply(lambda x : 0 if len(engager_follows_creator[x['engager_id']]) > 0 and x['creator_id'] in engager_follows_creator[x['engager_id']]  else 0.5, axis = 1)



<ipython-input-55-82faeb8cac16>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  b['engager_follows_creator'] = b.apply(lambda x : 0 if len(engager_follows_creator[x['engager_id']]) > 0 and x['creator_id'] in engager_follows_creator[x['engager_id']]  else 0.5, axis = 1)


In [58]:
b = b[b['engager_follows_creator'] != 0.5]



In [54]:
engager_follows_creator

defaultdict(<function __main__.<lambda>()>,
            {'66C019BF51691BDD20F8DCF68E3802D3': {'0946688749E92C955D0EAA0FA4DE06BC',
              '32228C9CB81C56CA048F10F552B169BB',
              '3752D0EFA734C59383F9A00CBB257F81',
              '56BA35D9BCB8E43A6A2A0AB1701E90AD',
              'A088167C2D84B53F1D0B504B541295A5',
              'BEFA5695D44BCC8220761214DB14EBBF'},
             'ECBEBBA9924FE35ECAB9BE900B7B1DEE': {'3AAEF4AB24C95D9520DC832A38A9D136',
              '3FE07F2D7C0F2784FDCEA49CE7E2437C',
              '53CE2042F26C16E633E206D7940D7058'},
             '1EBC671E39BC48BCAC8F36BD6F84697E': {'517B38585279F47C673B7C6476254CA3',
              '538117C87D3E183D88DBBC04365ADAFE',
              '6DC107ED87B63189FBCBFB4B6714DED5',
              'AEA5FE94F0A9AAAE0805A331B1E35E9B'},
             'B09360C73D80DD77E4B30F65CA95905D': {'08846D9BB65ADBCBD3E8B1C484C06C14',
              '1D2BA8DA427A75F0017456DF0D38B741',
              '2AC773B51CC65ACEB5CA2AD3B6976E6B',
         

In [2]:
from Ensemble_FFNN_ALL import Ensemble_FFNN_ALL
from network import Network

In [5]:
class Train(object):
    def __init__(self, target='ensemble', ensemble_num=0):
        self.df = Dataiter(conf.small_dataset_path, ensemble_num, train=True) 
        
        model = Ensemble_FFNN_ALL(self.df)
        self.model = Network(model)
        
    def train(self):
        self.model.train() 
    

In [6]:
Train().train()

0it [00:00, ?it/s]

reply ['reply', 'retweet', 'comment', 'like']
32/32 [==============================] - 0s 467us/step - loss: 0.2718 - binary_crossentropy: 0.2718
INFO:tensorflow:Assets written to: /hdd/models/ensemble_ffnn_pkl//ensemble-0/ffnn--reply-0/assets
retweet ['reply', 'retweet', 'comment', 'like']
32/32 [==============================] - 0s 482us/step - loss: 0.3301 - binary_crossentropy: 0.3301
INFO:tensorflow:Assets written to: /hdd/models/ensemble_ffnn_pkl//ensemble-0/ffnn--retweet-0/assets
comment ['reply', 'retweet', 'comment', 'like']
32/32 [==============================] - 0s 465us/step - loss: 0.1105 - binary_crossentropy: 0.1105
INFO:tensorflow:Assets written to: /hdd/models/ensemble_ffnn_pkl//ensemble-0/ffnn--comment-0/assets
like ['reply', 'retweet', 'comment', 'like']
32/32 [==============================] - 0s 463us/step - loss: 1.1559 - binary_crossentropy: 1.1559
INFO:tensorflow:Assets written to: /hdd/models/ensemble_ffnn_pkl//ensemble-0/ffnn--like-0/assets


1it [02:06, 126.05s/it]


### Test defalut values

In [3]:
import numpy as np
from utils.preprocessing import *

from utils.dataiter import Dataset



In [4]:
path = '/dataset/final_data/small_dataset/valid_1000'

ds = Dataset()
df = read_data(path)

# df = ds.preprocess(df, TARGET_id=conf.REPLY)
# df = ds.tweet_engagements(df) # tweet engagement
# df = ds.user_engagements(df, train = False) # user engagement
# df = ds.tweet_features(df) # tweet features


In [6]:
result = []
result.append(df['like_timestamp'])
result.append(df['like_timestamp'])
result.append(df['like_timestamp'])
result.append(df['like_timestamp'])

In [9]:
np.mean(result, axis=0)

array([1.61467532e+09,            nan,            nan, 1.61435657e+09,
                  nan, 1.61471720e+09,            nan,            nan,
                  nan, 1.61435175e+09, 1.61441245e+09,            nan,
                  nan, 1.61480760e+09,            nan, 1.61432289e+09,
       1.61431192e+09,            nan,            nan, 1.61469100e+09,
                  nan,            nan,            nan, 1.61463042e+09,
       1.61477746e+09, 1.61463519e+09,            nan,            nan,
       1.61429671e+09,            nan,            nan, 1.61445400e+09,
                  nan,            nan,            nan,            nan,
       1.61477513e+09,            nan,            nan, 1.61455684e+09,
       1.61458779e+09, 1.61479940e+09, 1.61458315e+09, 1.61480674e+09,
                  nan,            nan, 1.61443386e+09,            nan,
                  nan,            nan,            nan,            nan,
                  nan, 1.61478541e+09, 1.61436307e+09,            nan,
      

In [4]:
df = ds.fill_with_default_value(df) # fill_with_default_value



In [5]:
df

creator_id                        engager_id  \
0    7D3C3D00D14613287ABC9C140FE26A54  05DAD6CEF374FE6DBB6A845828C14E46   
1    6B1525449DEC20FFB77526D2A86B1563  F16C923EEEF0C56FA8E03C9947A70CAB   
2    437B4EF4128B8FE8079BB81A5ACF656C  86FADA0FC87B8668B34C4C9EA41EEF54   
3    96BD65F70F3659D17C532D17EE89E378  CF3CCAA5F335FC784FD5635CF433688C   
4    0076D50D707E65CA929490588036C58A  AC30E66EC27F4C07FE1278D6DDC2FBEB   
..                                ...                               ...   
995  1A29CB771DD6A60B7FA82E976D1F443E  5520031E463AE39929190362D1B0158A   
996  7F926A5A9325DA123273097D722F1FDC  5EE96FEA697E6FC790D527EE39C41C82   
997  C83B85B3AE3FEF0F3ABCBC20B4D1246F  5CC5BF471F3296B1BBCAEDEE8A30D92E   
998  E9B92A461DF7001852A34825E1FA19B0  3EFB8ACD4F892F5C6006C4107D9552D9   
999  EE7F586C29D822CA3AE006DCA3DB01B2  6F7298446E75BDEDBE2DA15216160901   

                             tweet_id  tweet_type  language  \
0    63F05256F79E7A098BF78E508967014B           0         2   
1    620B83CB3963A1A24D59AD1CDA2C1E10           3         3   
2    5614711FC32B65D6315447666196B362           0         1   
3    50733D80B3733168FBEBA7B7E6F76328           3         0   
4    9AF23572E97D092F188F89B98026F970           3         1   
..                                ...         ...       ...   
995  EF5691562CF48CF96029670C95D062A4           0         0   
996  BCD21BD3DD4FDF61AE5D77A05B929A3C           3         0   
997  67923B5FB2A45FAFA84C21070AD5F0F8           3         6   
998  BE521F3399E96F39B4B3D6A477A6E259           0         0   
999  FF86A97A2C65C7A9A9A69566C75B8AE9           0         2   

                             hashtags  creator_account_creation  \
0                                 NaN                1321444362   
1    A338C5C1637BEDA847BC1237241145BC                1359135965   
2                                 NaN                1383896999   
3                                 NaN                1247299050   
4                                 NaN                1411890034   
..                                ...                       ...   
995                               NaN                1484283705   
996                               NaN                1319910295   
997                               NaN                1560930109   
998                               NaN                1570555091   
999                               NaN                1577980139   

     creator_follower_count  creator_following_count  engager_follower_count  \
0                     17208                    14164                     437   
1                      5050                     4982                    1316   
2                       428                      608                     417   
3                  40626915                       64                       3   
4                       464                      345                     136   
..                      ...                      ...                     ...   
995                   11284                    12411                    8471   
996                   41306                     7051                     500   
997                   81629                      455                       4   
998                    2133                     1007                     442   
999                     869                      284                    3034   

     ...  creator_feature_number_of_previous_retweet_engagement  \
0    ...                                                  7       
1    ...                                                  3       
2    ...                                                  7       
3    ...                                                877       
4    ...                                                  0       
..   ...                                                ...       
995  ...                                                  0       
996  ...                                                 31       


### 10% 데이터를 임의로 default로 채우기

In [ ]:
tmp = df.sample(frac=0.1, # fraction of axis items to return. 
          random_state=1004)

In [ ]:
# defult value dict (나중에 피클로 불러오기)
default_values = {
    'creator_main_language' : 66, # unknown, OR 0 (=English) 
    'engager_main_language' : 66,
    'engager_feature_number_of_previous_like_engagement' : 7, # 나중에 평균으로 바뀔것
    'engager_feature_number_of_previous_reply_engagement' : 7,
    'engager_feature_number_of_previous_retweet_engagement' : 7,
    'engager_feature_number_of_previous_comment_engagement' : 7,
    'number_of_engagements_positive' : 7,
    'creator_feature_number_of_previous_like_engagement' : 7,
    'creator_feature_number_of_previous_reply_engagement' : 7,
    'creator_feature_number_of_previous_retweet_engagement' : 7,
    'creator_feature_number_of_previous_comment_engagement' : 7,
    'number_of_tweet_engagements' : 7,

    'creator_number_of_engagements_positive' : 0.7,
    'creator_number_of_engagements_ratio_reply' : 0.7,
    'creator_number_of_engagements_ratio_like' : 0.7,
    'creator_number_of_engagements_ratio_retweet' : 0.7,
    'creator_number_of_engagements_ratio_comment' : 0.7,
    'number_of_engagements_ratio_comment' : 0.7,
    'number_of_engagements_ratio_reply' : 0.7,
    'number_of_engagements_ratio_like': 0.7, 
    'number_of_engagements_ratio_retweet': 0.7,
    'is_tweet_in_creator_main_language': 0.5,
    'is_tweet_in_engager_main_language': 0.5,
}

In [ ]:
for key in default_values.keys():
    tmp[key] = default_values[key]

In [ ]:
tmp.index

In [ ]:
df.loc[tmp.index] = tmp.loc[tmp.index]

In [ ]:
df.loc[277]